## 1) Introduction/Business Problem<a id="Introduction/BusinessProblem"></a>

Introduction where you discuss the business problem and who would be interested in this project.

**_The main reason of this project is to help people who are planning to open a restaurant in the Toronto area. This study provides data about the competitors, population and income in different neighborhoods in Toronto._**

## 2) Downloading and Prepping Data<a id="#1"></a>

Data where you describe the data that will be used to solve the problem and the source of the data.

**_In order to provide the necessary data for this study I have used the population and the average income per neighborhood from Toronto’s 2016 Census. This information then has been combined with Foursquare API and Toronto’s neighborhood shape file to store data on competitors within the same area.
Links available to this data are listed below:_**

**_Toronto Neighborhoods' shape file https://open.toronto.ca/catalogue/?sort=last_refreshed%20desc_**

**_Toronto's Census 2016
https://open.toronto.ca/dataset/wellbeing-toronto-demographics/_**



Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [0]:
# !conda install -c conda-forge geopy --yes 
# !conda install -c conda-forge geocoder --yes
# !conda install -c conda-forge/label/gcc7 geopandas --yes
# !conda install -c conda-forge folium=0.5.0 --yes

In [0]:
import numpy as np

import json

import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.options.mode.chained_assignment = None  

import time

import geopy
from geopy.geocoders import Nominatim

import geocoder

import geopandas as gpd

import folium
from folium.plugins import HeatMap

import requests 
from pandas.io.json import json_normalize 

import csv

print('Libraries imported.')

Libraries imported.


### 2.1) Download and Explore Datasets

#### 2.1.1) Loading Toronto's 2016 Census into a dataframe

In [0]:
csv_path='https://www.toronto.ca/ext/open_data/catalog/data_set_files/2016_neighbourhood_profiles.csv'
df = pd.read_csv(csv_path, thousands=',',encoding='latin1')
print('Data loaded')

**Data Sample**

Exploring collected data

In [0]:
df.head()

Category                      Topic  \
0  Neighbourhood Information  Neighbourhood Information   
1  Neighbourhood Information  Neighbourhood Information   
2                 Population   Population and dwellings   
3                 Population   Population and dwellings   
4                 Population   Population and dwellings   

                      Data Source               Characteristic  \
0                 City of Toronto         Neighbourhood Number   
1                 City of Toronto         TSNS2020 Designation   
2  Census Profile 98-316-X2016001             Population, 2016   
3  Census Profile 98-316-X2016001             Population, 2011   
4  Census Profile 98-316-X2016001  Population Change 2011-2016   

  City of Toronto Agincourt North Agincourt South-Malvern West  \
0             NaN             129                          128   
1             NaN  No Designation               No Designation   
2       2,731,571          29,113                       23,757   
3       2,615,060          30,279                       21,988   
4           4.50%          -3.90%                        8.00%   

        Alderwood           Annex Banbury-Don Mills  Bathurst Manor  \
0              20              95                42              34   
1  No Designation  No Designation    No Designation  No Designation   
2          12,054          30,526            27,695          15,873   
3          11,904          29,177            26,918          15,434   
4           1.30%           4.60%             2.90%           2.80%   

  Bay Street Corridor Bayview Village Bayview Woods-Steeles  \
0                  76              52                    49   
1      No Designation  No Designation        No Designation   
2              25,797          21,396                13,154   
3              19,348          17,671                13,530   
4              33.30%          21.10%                -2.80%   

  Bedford Park-Nortown Beechborough-Greenbrook         Bendale  \
0                   39                     112             127   
1       No Designation                     NIA  No Designation   
2               23,236                   6,577          29,960   
3               23,185                   6,488          27,876   
4                0.20%                   1.40%           7.50%   

  Birchcliffe-Cliffside Black Creek     Blake-Jones Briar Hill-Belgravia  \
0                   122          24              69                  108   
1        No Designation         NIA  No Designation       No Designation   
2                22,291      21,737           7,727               14,257   
3                21,856      22,057           7,763               14,302   
4                 2.00%      -1.50%          -0.50%               -0.30%   

  Bridle Path-Sunnybrook-York Mills Broadview North Brookhaven-Amesbury  \
0                                41              57                  30   
1                    No Designation  No Designation      No Designation   
2                             9,266          11,499              17,757   
3                             8,713          11,563              17,787   
4                             6.30%          -0.60%              -0.20%   

  Cabbagetown-South St. James Town Caledonia-Fairbank       Casa Loma  \
0                               71                109              96   
1                   No Designation     No Designation  No Designation   
2                           11,669              9,955          10,968   
3                           12,053              9,851          10,487   
4                           -3.20%              1.10%           4.60%   

  Centennial Scarborough Church-Yonge Corridor Clairlea-Birchmount  \
0                    133                    75                 120   
1         No Designation        No Designation      No Designation   
2                 13,362                31,340              26,984   
3                 13,093                2

#### 2.1.2) Collecting neighborhoods names

In [0]:
Neighbourhoods = list(df.columns.values)
Neighbourhoods = Neighbourhoods[5:]
print(Neighbourhoods)

['Agincourt North', 'Agincourt South-Malvern West', 'Alderwood', 'Annex', 'Banbury-Don Mills', 'Bathurst Manor', 'Bay Street Corridor', 'Bayview Village', 'Bayview Woods-Steeles', 'Bedford Park-Nortown', 'Beechborough-Greenbrook', 'Bendale', 'Birchcliffe-Cliffside', 'Black Creek', 'Blake-Jones', 'Briar Hill-Belgravia', 'Bridle Path-Sunnybrook-York Mills', 'Broadview North', 'Brookhaven-Amesbury', 'Cabbagetown-South St. James Town', 'Caledonia-Fairbank', 'Casa Loma', 'Centennial Scarborough', 'Church-Yonge Corridor', 'Clairlea-Birchmount', 'Clanton Park', 'Cliffcrest', 'Corso Italia-Davenport', 'Danforth', 'Danforth East York', 'Don Valley Village', 'Dorset Park', 'Dovercourt-Wallace Emerson-Junction', 'Downsview-Roding-CFB', 'Dufferin Grove', 'East End-Danforth', 'Edenbridge-Humber Valley', 'Eglinton East', 'Elms-Old Rexdale', 'Englemount-Lawrence', 'Eringate-Centennial-West Deane', 'Etobicoke West Mall', 'Flemingdon Park', 'Forest Hill North', 'Forest Hill South', 'Glenfield-Jane Heig

#### 2.1.3) Collecting Population and Average Income per neighborhood

Creating a new dataset

In [0]:
dfToronto = pd.DataFrame(index=Neighbourhoods, columns=['Population_2016','Income_2016','Neighbourhood_Number'])

Populating the dataset with the data

In [0]:
# Population_2016 = Population, 2016
# Income_2016 = Total income: Average amount ($)

for index, row in dfToronto.iterrows():
    dfToronto.at[index, 'Population_2016'] = df[index][2]
    dfToronto.at[index, 'Income_2016'] = df[index][2264]
    dfToronto.at[index, 'Neighbourhood_Number'] = df[index][0]

dfToronto['Population_2016'] = dfToronto['Population_2016'].str.replace(',','.').astype(float)
dfToronto['Income_2016'] = dfToronto['Income_2016'].str.replace(',','.').astype(float)

dfToronto = dfToronto.sort_values('Income_2016', ascending=0)
dfToronto.head()

Population_2016  Income_2016  \
Bridle Path-Sunnybrook-York Mills            9.266      308.010   
Rosedale-Moore Park                         20.923      207.903   
Forest Hill South                           10.732      204.521   
Lawrence Park South                         15.179      169.203   
Casa Loma                                   10.968      165.047   

                                  Neighbourhood_Number  
Bridle Path-Sunnybrook-York Mills                   41  
Rosedale-Moore Park                                 98  
Forest Hill South                                  101  
Lawrence Park South                                103  
Casa Loma                                           96

Toronto Open Data website provides a shapefile with all neighbourhoods.NEIGHBORHOODS_WGS84.shp can be found on https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/#a45bd45a-ede8-730e-1abc-93105b2c439f


Coverting shapefile to json using shp2gj.py - https://gist.github.com/frankrowe/6071443 

In [0]:
import shapefile

# read the shapefile
reader = shapefile.Reader("NEIGHBORHOODS_WGS84.shp")
fields = reader.fields[1:]
field_names = [field[0] for field in fields]
buffer = []
for sr in reader.shapeRecords():
    atr = dict(zip(field_names, sr.record))
    geom = sr.shape.__geo_interface__
    buffer.append(dict(type="Feature", geometry=geom, properties=atr))

# write the GeoJSON file
from json import dumps
geojson = open("torontoNeighbourhoods.json", "w")
geojson.write(dumps({"type": "FeatureCollection","features": buffer}, indent=2) + "\n")
geojson.close()

print("torontoNeighbourhoods.json created!")

torontoNeighbourhoods.json created!


#### 2.1.4) Collecting geocodes for each neighborhood

In [0]:
dfToronto['Latitude'] = pd.Series("", index=dfToronto.index)
dfToronto['Longitude'] = pd.Series("", index=dfToronto.index)
dfToronto.reset_index()


index  Population_2016  Income_2016  \
0      Bridle Path-Sunnybrook-York Mills            9.266      308.010   
1                    Rosedale-Moore Park           20.923      207.903   
2                      Forest Hill South           10.732      204.521   
3                    Lawrence Park South           15.179      169.203   
4                              Casa Loma           10.968      165.047   
5                         Kingsway South            9.271      144.642   
6                     Leaside-Bennington           16.828      125.564   
7                   Bedford Park-Nortown           23.236      123.077   
8                         Yonge-St.Clair           12.528      114.174   
9                                  Annex           30.526      112.766   
10                   Lawrence Park North           14.607      111.730   
11              Edenbridge-Humber Valley           15.535      101.551   
12                  St.Andrew-Windfields           17.812      100.516   
13                    Princess-Rosethorn           11.051       99.055   
14                           The Beaches           21.567       92.580   
15                        Yonge-Eglinton           11.817       89.330   
16                   Mount Pleasant East           16.775       85.340   
17                     Forest Hill North           12.806       85.099   
18                    Lambton Baby Point            7.985       76.629   
19                       North Riverdale           11.916       73.253   
20                      Lansing-Westgate           16.164       72.371   
21          Runnymede-Bloor West Village           10.070       71.888   
22                     High Park-Swansea           23.925       71.204   
23              Playter Estates-Danforth            7.804       70.831   
24                               Niagara           31.180       70.623   
25     Waterfront Communities-The Island           65.913       70.600   
26                     Banbury-Don Mills           27.695       67.757   
27                    Humewood-Cedarvale           14.365       65.274   
28                   Stonegate-Queensway           25.051       64.140   
29      Cabbagetown-South St. James Town           11.669       63.012   
30                         Markland Wood           10.554       62.378   
31                             Moss Park           20.506       58.915   
32               Palmerston-Little Italy           13.826       58.071   
33                       High Park North           22.162       57.465   
34                   Mount Pleasant West           29.658       57.039   
35                   Bay Street Corridor           25.797       56.526   
36                              Danforth            9.666       55.225   
37                     Woodbine Corridor           12.541       55.199   
38                              Wychwood           14.349       54.460   
39   Mimico (includes Humber Bay Shores)           33.964       54.438   
40                 Birchcliffe-Cliffside           22.291       54.360   
41                     East End-Danforth           21.381       54.324   
42                Centennial Scarborough           13.362       54.045   
43                       South Riverdale           27.876       53.803   
44                 Church-Yonge Corridor           31.340       53.583   
45                         Old East York            9.233       53.315   
46                             Guildwood            9.917       53.203   
47            Islington-City Centre West           43.965       52.787   
48                       Bayview Village           21.396       52.035   
49                    Danforth East York           17.180       51.846   
50                          Clanton Park           16.472       51.181   
51                            University            7.607       50.757   
52                     Trinity-Bellwoods           16.556       50.694   
53                          Roncesvalle

In [0]:
dfToronto = pd.read_csv("dfToronto.csv", header = 0, names = column_names, sep=';')

#Convert Neighborhood IDs to string and add zeros at the begining to mathc with geoson file
#Normalize data Neighbourhood_Number must have 3 digits to math the json ID
dfToronto['Neighbourhood_Number'] = dfToronto['Neighbourhood_Number'].astype(str)
for index, row in dfToronto.iterrows():
    if len(dfToronto.at[index, 'Neighbourhood_Number']) == 1:
        dfToronto.at[index, 'Neighbourhood_Number'] =  "00" + dfToronto.at[index, 'Neighbourhood_Number']
    if len(dfToronto.at[index, 'Neighbourhood_Number']) == 2:
        dfToronto.at[index, 'Neighbourhood_Number'] =  "0" + dfToronto.at[index, 'Neighbourhood_Number']
        
dfToronto.head()

Neighborhood  Population_2016  Income_2016  \
0  Bridle Path-Sunnybrook-York Mills            9.266      308.010   
1                Rosedale-Moore Park           20.923      207.903   
2                  Forest Hill South           10.732      204.521   
3                Lawrence Park South           15.179      169.203   
4                          Casa Loma           10.968      165.047   

  Neighbourhood_Number   Latitude  Longitude  
0                  041        NaN        NaN  
1                  098  43.690388 -79.383297  
2                  101  43.693559 -79.413902  
3                  103  43.729199 -79.403253  
4                  096  43.678111 -79.409408

#### 2.1.5) Creating a new map of Toronto and Choropleth

In [0]:
#https://www.toronto.ca/city-government/data-research-maps/open-data/open-data-catalogue/#a45bd45a-ede8-730e-1abc-93105b2c439f

#Use geopy library to get the latitude and longitude values of Toronto
address = 'Toronto,ON'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


#### 2.1.6) Toronto's Income per Neighborhood

In [0]:
# Load the shape of the neighborhoods
state_geo = 'torontoNeighbourhoods.json'

# Initialize the map:
m = folium.Map(tiles='Stamen Terrain', location=[latitude+0.05, longitude+0.1], zoom_start=11)

# Add the color for the Income_2016 choropleth:
m.choropleth(
 geo_data=state_geo,
 name='Income_2016',
 data=dfToronto,
 columns=['Neighbourhood_Number', 'Income_2016'],
 key_on='properties.AREA_S_CD',
 fill_color='YlGn',
 fill_opacity=0.5,
 line_opacity=0.5,
 legend_name='Income 2016'
)
m.add_child(folium.map.LayerControl())
    
# Save to html
m

#### 2.1.7) Toronto's Population per Neighborhood

In [0]:
# Initialize the map:
m1 = folium.Map(tiles='Stamen Terrain', location=[latitude+0.05, longitude+0.1], zoom_start=11)

# Add the color for the Population_2016 choropleth:
m1.choropleth(
    geo_data=state_geo,
    name='Population_2016',
    data=dfToronto,
    columns=['Neighbourhood_Number', 'Population_2016'],
    key_on='properties.AREA_S_CD',
    fill_color='YlOrRd',
    fill_opacity=0.5,
    line_opacity=0.5,
    legend_name='Population 2016'
)

m1.add_child(folium.map.LayerControl())

# Save to html
m1

In [0]:
# Initialize the map:
m2 = folium.Map(tiles='Stamen Terrain', location=[latitude+0.05, longitude+0.1], zoom_start=11)

for i in range(len(dfToronto)):
    try: 
        folium.Marker(location=[dfToronto['Latitude'][i], dfToronto['Longitude'][i]],
                      popup=folium.Popup(dfToronto['Neighborhood'][i], parse_html=True)
                      ).add_to(m2)
    except: 
        pass
    
m2

#### 2.1.8) Utilizing the Foursquare API to explore the neighborhoods venues

In [0]:
#### Define Foursquare Credentials and Version

CLIENT_ID = 'xxxxxxxxxxxxxx' # your Foursquare ID
CLIENT_SECRET = 'xxxxxxxxxxxxxxxxx' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

In [0]:
LIMIT = 100
RADIUS = 500

# function that extracts the category of the venue
def getNearbyVenues(name, lat, lng, radius=500):
    
    venues_list=[]

    # create the API request URL
    url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
        CLIENT_ID, 
        CLIENT_SECRET, 
        VERSION, 
        lat, 
        lng, 
        radius, 
        LIMIT)

    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']

    # return only relevant information for each nearby venue
    venues_list.append([(
        name, 
        lat, 
        lng, 
        v['venue']['name'], 
        v['venue']['location']['lat'], 
        v['venue']['location']['lng'],  
        v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [0]:
## List all venues of all neighborhoods

nearby_venues = pd.DataFrame()

for i in range(len(dfToronto)):
    try: 
        print(".",end="")
        nearby_venues = nearby_venues.append(getNearbyVenues(name=dfToronto['Neighborhood'][i], lat=dfToronto['Latitude'][i], lng=dfToronto['Longitude'][i]))
    except: 
        pass


nearby_venues.head()

............................................................................................................................................

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Rosedale-Moore Park              43.690388              -79.383297   
1  Rosedale-Moore Park              43.690388              -79.383297   
2  Rosedale-Moore Park              43.690388              -79.383297   
3  Rosedale-Moore Park              43.690388              -79.383297   
4  Rosedale-Moore Park              43.690388              -79.383297   

                           Venue  Venue Latitude  Venue Longitude  \
0                   Pure Fitness       43.693007       -79.387781   
1         Moore Park Tennis Club       43.693289       -79.382900   
2                 Moorevale Park       43.693610       -79.383465   
3  Mount Pleasant Road And Moore       43.693560       -79.384600   
4                     On The Run       43.693410       -79.386506   

      Venue Category  
0                Gym  
1       Tennis Court  
2         Playground  
3       Intersection  
4  Convenience Store

In [0]:
print('There are {} uniques categories.'.format(len(nearby_venues['Venue Category'].unique())))

nearby_venues['Venue Category'].unique()

There are 260 uniques categories.


array(['Gym', 'Tennis Court', 'Playground', 'Intersection',
       'Convenience Store', 'Bank', 'Arts & Crafts Store', 'Park',
       'Accessories Store', 'Mediterranean Restaurant', 'Bakery',
       'Tea Room', 'Bubble Tea Shop', 'Ice Cream Shop',
       'Toy / Game Store', 'BBQ Joint', 'Burger Joint',
       'Japanese Restaurant', 'Asian Restaurant', 'Sushi Restaurant',
       'Café', 'Coffee Shop', 'Pub', 'Italian Restaurant', 'Diner',
       'Hobby Shop', 'Frozen Yogurt Shop', 'Pharmacy', 'Pizza Place',
       'Lingerie Store', 'Cosmetics Shop', 'Seafood Restaurant',
       'Sandwich Place', 'Gastropub', 'Dance Studio', 'Bus Line',
       'Fast Food Restaurant', 'Mobile Phone Shop', 'Pool',
       'Salon / Barbershop', 'Shoe Store', 'Shopping Mall',
       'Metro Station', 'Massage Studio', 'Deli / Bodega', 'Spa',
       'Castle', 'Historic Site', 'Museum', 'History Museum',
       'Indian Restaurant', 'French Restaurant', 'Steakhouse',
       'Vegetarian / Vegan Restaurant', 'Thea

In [0]:
## Filter only the "Restaurants" out of all venues 
nearby_restaurants = pd.DataFrame()

nearby_restaurants = nearby_venues[nearby_venues['Venue Category'].str.contains("Restaurant")]
nearby_restaurants.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
5     Forest Hill South              43.693559              -79.413902   
7   Lawrence Park South              43.729199              -79.403253   
8   Lawrence Park South              43.729199              -79.403253   
10  Lawrence Park South              43.729199              -79.403253   
16  Lawrence Park South              43.729199              -79.403253   

                          Venue  Venue Latitude  Venue Longitude  \
5   Sofra Mediterranean Cuisine       43.689251       -79.412882   
7         Shinobu by Maki Sushi       43.732562       -79.404147   
8                     Riz North       43.730792       -79.403719   
10                     Shoushin       43.731380       -79.403961   
16                  Yonge Sushi       43.733182       -79.404323   

              Venue Category  
5   Mediterranean Restaurant  
7        Japanese Restaurant  
8           Asian Restaurant  
10          Sushi Restaurant  
16          Sushi Restaurant

#### 2.1.9) Listing restaurants in the map

In [0]:
# Initialize the map:
m3 = folium.Map(tiles='Stamen Terrain', location=[latitude+0.05, longitude+0.1], zoom_start=11)

nearby_restaurants['Venue Latitude'] = pd.to_numeric(nearby_restaurants['Venue Latitude'], errors='coerce').fillna(0)
nearby_restaurants['Venue Longitude'] = pd.to_numeric(nearby_restaurants['Venue Longitude'], errors='coerce').fillna(0)

for la, lo, ve in zip(nearby_restaurants['Venue Latitude'],nearby_restaurants['Venue Longitude'],nearby_restaurants['Venue']):
    try:
        m3.add_child(folium.Marker(location=[la,lo],popup=folium.Popup(ve,parse_html=True),icon=folium.Icon(icon='info-sign', color='green')))
    except:
        print("error")

m3

## 3) Methodology

Methodology section which represents the main component of the report where you discuss and describe any exploratory data analysis that you did, any inferential statistical testing that you performed, and what machine learnings were used and why.

**_In this report I have used various maps to help an individual/investor better decide in which neighborhood to open a new restaurant based on population, income and competition. In order to originate these maps, I used data from Foursquare to display the restaurants in the neighborhoods currently and used Toronto’s Census 2016 combined with choropleth to determine the population and income in each region._**

## 4) Results

Results section where you discuss the results.

**_As you can notice on the maps majority of the restaurants are located on the south side and main streets of Toronto. We can also see that most of the high income neighborhoods are located up north. It was also noticed that a more population in an area did not reflect upon the number of restaurants in the area._**

## 5) Discussion

Discussion section where you discuss any observations you noted and any recommendations you can make based on the results.

**_At the beginning of this project I was expecting to find clusters of restaurants in different locations of Toronto and in the end the results did not meet my hypothesis._**

## 6) Conclusion

Conclusion section where you conclude the report.

**_In conclusion, this study can be useful for investors who are looking to open a new restaurant in Toronto by comparing different neighborhood profiles based on income, population and competition. This study only use’s a few variables to conduct research so it does not cover all variables that may also need to be taken into consideration therefore this study can not be used as a single decision making tool for an individual/investor._**